In [3]:
import pandas as pd
from mlxtend.frequent_patterns import apriori, association_rules
from mlxtend.preprocessing import TransactionEncoder

df = pd.read_csv("./heart.csv")

numerical_columns = df.columns[2:7] 
numerical_columns = ['Age', 'RestingBP', 'Cholesterol', 'FastingBS', 'MaxHR', 'Oldpeak']
medians = df[numerical_columns].median()

transactions = []

for index, row in df.iterrows():
    transaction = []
    for col in numerical_columns:
        if row[col] > medians[col]:
            transaction.append(f"{col}_high")
        else:
            transaction.append(f"{col}_low")
    if transaction: 
        transactions.append(transaction)

encoder = TransactionEncoder()
encoded_array = encoder.fit(transactions).transform(transactions)
encoded_df = pd.DataFrame(encoded_array, columns=encoder.columns_)

frequent_itemsets = apriori(encoded_df, min_support=0.1, use_colnames=True, low_memory=True)

num_itemsets = len(frequent_itemsets)

rules = association_rules(
    df=frequent_itemsets,
    num_itemsets=num_itemsets,
    metric="confidence",
    min_threshold=0.6
)

print("Часто встречающиеся наборы элементов:")
print(frequent_itemsets)

print("\nКоличество найденных наборов:", num_itemsets)

print("\nАссоциативные правила:")
print(rules)


Часто встречающиеся наборы элементов:
      support                                           itemsets
0    0.486928                                         (Age_high)
1    0.513072                                          (Age_low)
2    0.490196                                 (Cholesterol_high)
3    0.509804                                  (Cholesterol_low)
4    0.233115                                   (FastingBS_high)
..        ...                                                ...
203  0.137255  (Cholesterol_low, Oldpeak_low, RestingBP_low, ...
204  0.174292  (MaxHR_high, Oldpeak_low, RestingBP_low, Fasti...
205  0.112200  (Oldpeak_high, FastingBS_low, MaxHR_low, Resti...
206  0.113290  (Oldpeak_low, Cholesterol_high, FastingBS_low,...
207  0.139434  (Oldpeak_low, RestingBP_low, FastingBS_low, Ma...

[208 rows x 2 columns]

Количество найденных наборов: 208

Ассоциативные правила:
                                           antecedents  \
0                                     (Fa

In [7]:
import pandas as pd
from mlxtend.frequent_patterns import fpgrowth, association_rules
from mlxtend.preprocessing import TransactionEncoder

# Чтение данных
df = pd.read_csv('./heart.csv')

# Преобразование числовых столбцов в категориальные
df_binned = df.copy()

# Преобразуем числовые столбцы в категориальные (Low, High)
for column in df.columns:
    if column not in ['HeartDisease']:  # Исключаем целевую переменную
        if df[column].dtype in ['int64', 'float64']:  # Применяем к числовым столбцам
            df_binned[column] = pd.cut(df[column], bins=2, labels=["Low", "High"])

df_binned['HeartDisease'] = df['HeartDisease']  # Добавляем целевую переменную без изменений

# Преобразуем все данные в строки
df_binned = df_binned.applymap(str)

# Преобразуем данные в список транзакций
transactions = df_binned.apply(lambda x: x.tolist(), axis=1).tolist()

# Преобразование в формат, который поддерживает TransactionEncoder
te = TransactionEncoder()
te_ary = te.fit(transactions).transform(transactions)
df_transactions = pd.DataFrame(te_ary, columns=te.columns_)

# Применение FP-Growth для нахождения частых наборов
frequent_itemsets = fpgrowth(df_transactions, min_support=0.05, use_colnames=True)

# Получение числа частых наборов
num_itemsets = len(frequent_itemsets)

# Вывод частых наборов
print("Частые наборы:")
print(frequent_itemsets)

# Получение ассоциативных правил
rules = association_rules(
    df=frequent_itemsets,
    num_itemsets=num_itemsets,
    metric="confidence",
    min_threshold=0.8
)

# Вывод ассоциативных правил
print("\nАссоциативные правила:")
print(rules)


C:\Users\nik85\AppData\Local\Temp\ipykernel_22232\1893425376.py:20: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_binned = df_binned.applymap(str)


Частые наборы:
       support                itemsets
0     0.998911                  (High)
1     0.997821                   (Low)
2     0.789760                     (M)
3     0.601307                (Normal)
4     0.595861                     (N)
...        ...                     ...
1316  0.053377          (Down, 1, Low)
1317  0.053377    (Down, High, 1, Low)
1318  0.050109       (ASY, Down, High)
1319  0.050109        (ASY, Down, Low)
1320  0.050109  (ASY, Down, High, Low)

[1321 rows x 2 columns]

Ассоциативные правила:
            antecedents  consequents  antecedent support  consequent support  \
0                (High)        (Low)            0.998911            0.997821   
1                 (Low)       (High)            0.997821            0.998911   
2                   (M)       (High)            0.789760            0.998911   
3                   (M)        (Low)            0.789760            0.997821   
4             (M, High)        (Low)            0.788671            

In [9]:
import pandas as pd
from mlxtend.frequent_patterns import fpgrowth, association_rules
from mlxtend.preprocessing import TransactionEncoder

# Загружаем данные
df = pd.read_csv('./heart.csv')

# Убираем столбец с ID, если он есть (не присутствует в ваших данных, но на всякий случай)
# df.drop(columns=['id'], inplace=True)

# Биннинг числовых столбцов на 2 категории (Low/High)
df_binned = df.copy()
for column in df.columns:
    if column not in ['HeartDisease']:  # Оставляем целевую переменную без изменений
        if df[column].dtype in ['int64', 'float64']:  # Проверка, что столбец числовой
            df_binned[column] = pd.cut(df[column], bins=2, labels=["Low", "High"])

# Преобразуем все значения в строки, чтобы избежать ошибок при применении TransactionEncoder
df_binned = df_binned.astype(str)

# Формируем транзакции, где каждая строка - это список значений
transactions = df_binned.apply(lambda x: x.tolist(), axis=1).tolist()

# Преобразуем данные для использования в модели с помощью TransactionEncoder
te = TransactionEncoder()
te_ary = te.fit(transactions).transform(transactions)
df_transactions = pd.DataFrame(te_ary, columns=te.columns_)

# Применяем алгоритм FP-Growth для поиска частых наборов
frequent_itemsets = fpgrowth(df_transactions, min_support=0.05, use_colnames=True)

# Генерируем ассоциативные правила
rules = association_rules(
    df=frequent_itemsets,
    num_itemsets=len(frequent_itemsets),
    metric="confidence",
    min_threshold=0.5
)

# Выводим результаты
print("Частые наборы товаров на основе категорий:")
print(frequent_itemsets)

print("\nАссоциативные правила:")
print(rules)


Частые наборы товаров на основе категорий:
       support                itemsets
0     0.998911                  (High)
1     0.997821                   (Low)
2     0.789760                     (M)
3     0.601307                (Normal)
4     0.595861                     (N)
...        ...                     ...
1316  0.053377          (Down, 1, Low)
1317  0.053377    (Down, High, 1, Low)
1318  0.050109       (ASY, Down, High)
1319  0.050109        (ASY, Down, Low)
1320  0.050109  (ASY, Down, High, Low)

[1321 rows x 2 columns]

Ассоциативные правила:
             antecedents       consequents  antecedent support  \
0                 (High)             (Low)            0.998911   
1                  (Low)            (High)            0.997821   
2                    (M)            (High)            0.789760   
3                 (High)               (M)            0.998911   
4                    (M)             (Low)            0.789760   
...                  ...               ...  

In [10]:
import pandas as pd
from fpgrowth_py import fpgrowth

# Загружаем данные
df = pd.read_csv('heart.csv')  # Указываем путь к твоему файлу

# Убираем колонку ID (если она есть)
# df.drop(columns=['id'], inplace=True)  # Столбец 'id' у тебя в данных нет, поэтому эту строку можно удалить

# Бинируем числовые столбцы для преобразования в категориальные значения (Low, High)
df_binned = df.copy()
for column in df.columns:
    if column not in ['HeartDisease']:  # Пропускаем целевую переменную 'HeartDisease'
        if df[column].dtype != 'object':  # Применяем бинирование только для числовых данных
            df_binned[column] = pd.cut(df[column], bins=2, labels=["Low", "High"])

# Преобразуем данные в формат транзакций
transactions = df_binned.apply(lambda x: x.tolist(), axis=1).tolist()

# Запускаем FP-Growth для поиска частых наборов и правил
minSupRatio = 0.05  # Минимальная поддержка
minConf = 0.5       # Минимальная уверенность

freq_itemsets, rules = fpgrowth(transactions, minSupRatio=minSupRatio, minConf=minConf)

# Выводим частые наборы
print("Частые наборы элементов:")
for itemset in freq_itemsets:
    print(itemset)

# Выводим правила ассоциации
print("\nПравила ассоциации:")
for rule in rules:
    print(rule)


Частые наборы элементов:
{'TA'}
{'TA', 'High'}
{'TA', 'High'}
{'TA', 'High'}
{'TA', 'High', 'Low'}
{'TA', 'High', 'Low'}
{'TA', 'High', 'Low'}
{'TA', 'High', 'Low'}
{'TA', 'High', 'Low'}
{'TA', 'High', 'Low'}
{'TA', 'High', 'Low'}
{'TA', 'High', 'Low'}
{'TA', 'Low'}
{'TA', 'Low'}
{'TA', 'Low'}
{'Down'}
{'ASY', 'Down'}
{'ASY', 'Down', 'Low'}
{'ASY', 'Down', 'Low'}
{'ASY', 'Down', 'Low'}
{'ASY', 'Down', 'High', 'Low'}
{'ASY', 'Down', 'High', 'Low'}
{'ASY', 'Down', 'High', 'Low'}
{'ASY', 'Down', 'High', 'Low'}
{'ASY', 'Down', 'High', 'Low'}
{'ASY', 'Down', 'High', 'Low'}
{'ASY', 'Down', 'High', 'Low'}
{'ASY', 'Down', 'High', 'Low'}
{'ASY', 'Down', 'High', 'Low'}
{'ASY', 'Down', 'High'}
{'ASY', 'Down', 'High'}
{'ASY', 'Down', 'High'}
{'Down', 1}
{'Down', 1, 'Low'}
{'Down', 1, 'Low'}
{'Down', 1, 'Low'}
{'Down', 'High', 1, 'Low'}
{'Down', 'High', 1, 'Low'}
{'Down', 'High', 1, 'Low'}
{'Down', 'High', 1, 'Low'}
{'Down', 'High', 1, 'Low'}
{'Down', 'High', 1, 'Low'}
{'Down', 'High', 1, 'Low'}
{'